In [136]:
from transformers import AutoTokenizer
from sentence_transformers import SentenceTransformer
import os
import chromadb
import re
import html
import copy
from llama_cpp import Llama
import gradio as gr
from IPython.display import Markdown, display

# Embed a folder of CERA webpages in txt format

## Embedding model and tokenizer

In [3]:
#embed_model_name = "dangvantuan/sentence-camembert-large"
#embed_model = HuggingFaceEmbedding(model_name=embed_model_name)

embed_model_name = 'intfloat/multilingual-e5-large'
tokenizer = AutoTokenizer.from_pretrained(embed_model_name)
embed_model = SentenceTransformer(embed_model_name)

/Users/peportier/miniforge3/envs/RAG_ENV/lib/python3.9/site-packages/transformers/utils/generic.py:309: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(


## Initialize a  ChromaDB persistent collection

In [58]:
chroma_client = chromadb.PersistentClient(path="./chromadb")
#chroma_client.delete_collection(name="cera")
collection = chroma_client.get_or_create_collection(name="cera")

## Embed the text of a particular web page

In [43]:
def token_length(str):
  return len(tokenizer.encode(str, add_special_tokens=False))

def passage_str(paragraphs, title):
    return f"passage: {title}\n" + '\n'.join(paragraphs)

In [57]:
def embed_page(filename, url, title, contents, tags, chroma_collection, embed_model, max_chunk_size=512):
    
    documents = []
    contents_to_embed = [contents]
    
    while contents_to_embed:
        last_item = contents_to_embed.pop()
        # (1) For the `multilingual-e5-large` embedding model, 
        # the string of a document must be prepended with "passage:"
        # (2) Since the text of a webpage may have to be cut into many documents,
        # we always add the title of the webpage at the top of a document
        last_item_str = passage_str(last_item, title)
        last_item_token_length = token_length(last_item_str)
        
        if last_item_token_length > max_chunk_size:
            # If the text of the webpage, present in file `filename`, 
            # contains more than `max_chunk_size` tokens, it must be divided 
            # into multiple documents
            if len(last_item) > 1:
                # If there are many paragraphs in `last_item`, i.e. the current
                # part of the webpage for which an embedding will be made,
                # the length of `last_item` can be reduced by dividing its set of
                # paragraphs in half
                h = len(last_item) // 2
                last_item_h1 = last_item[:h]
                last_item_h2 = last_item[h:]
                contents_to_embed.append(last_item_h1)
                contents_to_embed.append(last_item_h2)
            else:
                # If `last_item` is made of only one long paragraph whose length is
                # larger than `chunk_size`, this paragraph will be divided into two parts.
                sentences = re.split(r'(?<=[.!?]) +', last_item[0])
                
                if len(sentences) > 1:
                    # If there are multiple sentences, try to split into two parts
                    i = 1
                    while True:
                        part1 = ' '.join(sentences[:i])
                        part2 = ' '.join(sentences[i:])
                        token_length_part_1 = token_length(passage_str([part1], title))
                        token_length_part_2 = token_length(passage_str([part2], title))
                        if (token_length_part_1 <= max_chunk_size and
                            token_length_part_2 <= max_chunk_size) or \
                           token_length_part_1 > max_chunk_size:
                            break
                        i += 1
                else:
                    # If there's only one long sentence or no suitable split found, split by words
                    words = last_item[0].split()
                    h = len(words) // 2
                    part1 = ' '.join(words[:h])
                    part2 = ' '.join(words[h:])
                    
                contents_to_embed.append([part1])
                contents_to_embed.append([part2])
        else:
            documents.append(last_item_str)

    # We want the documents into which a webpage has been divided 
    # to be in the natural reading order
    documents.reverse()
    embeddings = embed_model.encode(documents, normalize_embeddings=True)
    embeddings = embeddings.tolist()

    # We consider the subpart of an URL as tags describing the webpage
    # For example, 
    # "https://www.caisse-epargne.fr/rhone-alpes/professionnels/financer-projets-optimiser-tresorerie/"
    # is associated to the tags:
    # tags[0] == 'rhone-alpes'
    # tags[1] == 'professionnels'
    # tags[2] == 'financer-projets-optimiser-tresorerie'
    if len(tags) < 2:
        category = ''
    else:
        if tags[0] == 'rhone-alpes':
            category = tags[1]
        else: category = tags[0]
    metadata = {'category': category, 'url': url}
    # All the documents corresponding to a same webpage have the same metadata, i.e. URL and category
    metadatas = [copy.deepcopy(metadata) for _ in range(len(documents))]

    ids = [filename + '-' + str(i+1) for i in range(len(documents))]

    chroma_collection.add(embeddings=embeddings, documents=documents, metadatas=metadatas, ids=ids)

## Embed all the webpages in a folder

In [45]:
def embed_folder(folder_path, chroma_collection, embed_model):
    for filename in os.listdir(folder_path):
        if filename.endswith('.txt'):
            file_path = os.path.join(folder_path, filename)
            with open(file_path, 'r') as file:
                file_contents = file.read()
            contents_lst = [str.replace('\n',' ').replace('\xa0', ' ') for str in file_contents.split('\n\n')]
            if len(contents_lst) < 3: # contents_lst[0] is the URL, contents_lst[1] is the title, the rest is the content
                continue
            url = contents_lst[0]
            if '?' in url: # URLs with a '?' corresponds to call to services and have no useful content
                continue
            title = contents_lst[1]
            if not title: # when the title is absent (or empty), the page has no interest
                continue
            print(f"{filename} : Start")
            prefix = 'https://www.caisse-epargne.fr/'
            suffix = url.replace(prefix, '')
            tags = suffix.split('/')
            tags = [tag for tag in tags if tag] # remove empty parts
            embed_page(filename, url, title, contents_lst[2:], tags, chroma_collection, embed_model)
            print(f"{filename} : Done")

## Proceed to the embedding

In [59]:
embed_folder('docs/cera2', collection, embed_model)

255a0eb096.txt : Start
255a0eb096.txt : Done
ce79680ee7.txt : Start
ce79680ee7.txt : Done
565b28a75b.txt : Start
565b28a75b.txt : Done
173fc21d3a.txt : Start
173fc21d3a.txt : Done
b3bd1cf160.txt : Start
b3bd1cf160.txt : Done
f73fb80f59.txt : Start
f73fb80f59.txt : Done
2b45bc13c2.txt : Start
2b45bc13c2.txt : Done
48787daff9.txt : Start
48787daff9.txt : Done
5f21a01035.txt : Start
5f21a01035.txt : Done
aa1030c5fd.txt : Start
aa1030c5fd.txt : Done
a040c90b55.txt : Start
a040c90b55.txt : Done
c3d469cbdb.txt : Start
c3d469cbdb.txt : Done
a6a1d2fea0.txt : Start
a6a1d2fea0.txt : Done
42a2928ef0.txt : Start
42a2928ef0.txt : Done
4eda4de449.txt : Start
4eda4de449.txt : Done
8cce840558.txt : Start
8cce840558.txt : Done
4a06529f5f.txt : Start
4a06529f5f.txt : Done
898d33ba09.txt : Start
898d33ba09.txt : Done
518b61af48.txt : Start
518b61af48.txt : Done
585b794776.txt : Start
585b794776.txt : Done
be98b7bc33.txt : Start
be98b7bc33.txt : Done
2e77392d24.txt : Start
2e77392d24.txt : Done
2db068af5c

# Query the ChromaDB collection

In [114]:
def query_collection(query, n_results=3):
    query = 'query: ' + query
    query_embedding = embed_model.encode(query, normalize_embeddings=True)
    query_embedding = query_embedding.tolist()
    results = collection.query(
        query_embeddings=[query_embedding],
        n_results=n_results,
    )
    return results

In [401]:
query = "Comment la Caisse d'Epargne Rhône-Alpes peut-elle aider une entreprise qui rencontre des problèmes de trésorerie ?"
query_results = query_collection(query)

# LLM model

In [9]:
llm = Llama(model_path='/Users/peportier/llm/a/a/zephyr-7b-beta.Q5_K_M.gguf', 
            n_gpu_layers=1, use_mlock=True, n_ctx=4096)

system_prompt = """\
Vous fournissez avec soin des réponses précises, factuelles, réfléchies et nuancées, et vous êtes doué pour le raisonnement. \
Si vous pensez qu'il n'y a peut-être pas de bonne réponse, vous le dites. \
Ne soyez pas verbeux dans vos réponses, mais donnez des détails et des exemples lorsque cela peut aider à l'explication. \
Vous rédigez vos réponses en français. \
"""

def format_prompt(question):
    prompt = ""
    prompt = f"<|system|>\n {system_prompt.strip()} </s>\n"
    prompt += f"<|user|>\n {question} </s>\n"
    prompt += f"<|assistant|>\n"
    return prompt

def answer(question):
    response = llm(prompt = question,
        temperature = 0.1,
        mirostat_mode = 2,
        max_tokens = -1,
        stop = ['</s>'])
    return response["choices"][0]["text"]

llama_model_loader: loaded meta data with 21 key-value pairs and 291 tensors from /Users/peportier/llm/a/a/zephyr-7b-beta.Q5_K_M.gguf (version GGUF V3 (latest))
llama_model_loader: - tensor    0:                token_embd.weight q5_K     [  4096, 32000,     1,     1 ]
llama_model_loader: - tensor    1:           blk.0.attn_norm.weight f32      [  4096,     1,     1,     1 ]
llama_model_loader: - tensor    2:            blk.0.ffn_down.weight q6_K     [ 14336,  4096,     1,     1 ]
llama_model_loader: - tensor    3:            blk.0.ffn_gate.weight q5_K     [  4096, 14336,     1,     1 ]
llama_model_loader: - tensor    4:              blk.0.ffn_up.weight q5_K     [  4096, 14336,     1,     1 ]
llama_model_loader: - tensor    5:            blk.0.ffn_norm.weight f32      [  4096,     1,     1,     1 ]
llama_model_loader: - tensor    6:              blk.0.attn_k.weight q5_K     [  4096,  1024,     1,     1 ]
llama_model_loader: - tensor    7:         blk.0.attn_output.weight q5_K     [  409

## Test LLM model

In [11]:
print(answer(format_prompt("Quels sont les philosophes les plus influencés par Hegel ?")))

Le philosophe allemand Georg Wilhelm Friedrich Hegel (1770-1831) a exercé une influence considérable sur la philosophie moderne, particulièrement dans le domaine de l'idéalisme et du marxisme. Voici quelques philosophes qui ont été fortement influencés par Hegel :

1. Karl Marx (1818-1883) : Le fondateur du marxisme a été profondément inspiré par la philosophie de Hegel, en particulier son concept d'histoire comme processus dialectique. Marx a critiqué et développé l'idée hégélienne de la dialectique pour expliquer le fonctionnement de la société et les lois de l'évolution historique.

2. Friedrich Engels (1820-1895) : Le collaborateur de Marx a également été influencé par Hegel, en particulier son concept d'histoire comme processus dialectique. Engels a développé cette idée dans son ouvrage "L'origine de la famille, de la propriété privée et de l'État" (1884), où il explique comment les relations sociales ont évolué en fonction des conditions historiques.

3. G.W.F. Hegel lui-même : C


llama_print_timings:        load time =     575.42 ms
llama_print_timings:      sample time =    2695.33 ms /   804 runs   (    3.35 ms per token,   298.29 tokens per second)
llama_print_timings: prompt eval time =     574.33 ms /   165 tokens (    3.48 ms per token,   287.29 tokens per second)
llama_print_timings:        eval time =   22009.23 ms /   803 runs   (   27.41 ms per token,    36.48 tokens per second)
llama_print_timings:       total time =   24988.34 ms


# RAG prompt

In [402]:
def format_passages(query_results):
    result = []
    for i in range(len(query_results["documents"][0])):
        passage = query_results["documents"][0][i]
        url = query_results["metadatas"][0][i]["url"]
        category = query_results["metadatas"][0][i]["category"]
        lines = passage.split('\n')
        if lines[0].startswith('passage: '):
            lines[0] = lines[0].replace('passage: ', '')
        lines.insert(0, "###")
        lines.insert(1, f"Passage {i+1}")
        lines.insert(2, "Titre :")
        lines.insert(4, "")
        lines.insert(5, "Catégorie :")
        lines.insert(6, category)
        lines.insert(7, "")
        lines.insert(8, "URL :")
        lines.insert(9, url)
        lines.insert(10, "")
        lines.insert(11, "Contenu : ")
        lines += ['']
        result += lines
    result = '\n'.join(result)
    return result
        

In [417]:
rag_system_prompt = """
Vous êtes un assistant IA qui répond à la question posée par l'utilisateur en utilisant un contexte répertorié ci-dessous dans la rubrique Contexte.
Le contexte est formé de passages exraits du site web commercial de la Caisse d'Epargne Rhône-Alpes, une banque française régionale.
Votre réponse ne doit pas mentionner des informations déjà présentes dans l'historique de la conversation qui est répertorié ci-dessous dans la rubrique Historique.
Vous fournissez avec soin des réponses précises, factuelles, réfléchies et nuancées, et vous êtes doué pour le raisonnement.
Toutes les informations factuelles que vous utilisez pour répondre proviennent exclusivement du contexte.
Si vous ne pouvez pas répondre à la question sur la base des éléments du contexte, dites simplement que vous ne savez pas, n'essayez pas d'inventer une réponse.
Vos réponses doivent être brèves.
Vous rédigez vos réponses en français au format markdown sous forme d'une liste d'au plus 7 éléments.
Voici le format que doit prendre votre réponse :
```
1. Elément de réponse. (Passage 1)
2. Elément de réponse. (Passage 1)
3. Elément de réponse. (Passage 2)
4. ...
```

----------------------------------------
Historique :
{history}
----------------------------------------
Contexte :
{context}
"""

def format_rag_prompt(query, context="", history=""):
    global chat_history
    
    user_query = f"Question de l'utilisateur : \n{query}\n\n"
    assistant_answer = f"Réponse de l'assistant : \n 1. "
    chat_history.append({'user': user_query, 'assistant': assistant_answer})

    system_prompt = rag_system_prompt.format(history=history, context=context)
    
    prompt = ""
    prompt = f"<|system|>\n{system_prompt.strip()} \n</s>\n"
    prompt += f"<|user|>\n{query} \n</s>\n"
    prompt += f"<|assistant|>\n Voici des éléments de réponse : \n 1. "
    
    return prompt

In [418]:
def answer_rag_prompt(query, query_results):
    global chat_history
    
    query_context = format_passages(query_results)

    history = ""
    for i in reversed(range(len(chat_history))):
        history += chat_history[i]["user"]
        history += chat_history[i]["assistant"]
        history += "\n\n"
    
    prompt = format_rag_prompt(query, query_context, history)
    
    ans = answer(prompt)
    chat_history[-1]['assistant'] += ans
    ans = '1. ' + ans
    
    return ans

In [419]:
chat_history = []

In [420]:
ans = answer_rag_prompt(query, query_results)

Llama.generate: prefix-match hit

llama_print_timings:        load time =     575.42 ms
llama_print_timings:      sample time =    7686.78 ms /  2270 runs   (    3.39 ms per token,   295.31 tokens per second)
llama_print_timings: prompt eval time =    4638.92 ms /  1729 tokens (    2.68 ms per token,   372.72 tokens per second)
llama_print_timings:        eval time =   80992.02 ms /  2269 runs   (   35.70 ms per token,    28.02 tokens per second)
llama_print_timings:       total time =   93681.23 ms


In [421]:
display(Markdown(ans))

1.  La Caisse d'Epargne Rhône Alpes propose un ensemble de solutions pour optimiser votre trésorerie sans attendre le règlement de vos factures clients, appelé l'affacturage. (Passage 1)
  2. Vous pouvez également accéder à leur simulateur et obtenir une préconisation sur le mode de financement le plus adapté à votre usage ainsi que de nombreuses informations sur la fiscalité automobile. (Passage 1)
  3. À taux fixe ou variable, les prêts classiques vous accompagnent dans le développement de votre entreprise. (Passage 1)
  4. La Caisse d'Epargne Rhône Alpes vous propose également un financement adapté pour vos projets de création, reprise ou développement de votre activité professionnelle avec un ensemble d'offres et de conseils pour vous accompagner dans le financement de vos projets. (Passage 1)
  5. En outre, la Caisse d'Epargne Rhône Alpes vous accompagne dans votre transition énergétique avec des offres sur mesure en fonction de vos besoins. (Passage 1)
  6. Vous pouvez également rencontrer un conseiller en ligne, à l'agence ou par téléphone à l'horaire de votre choix pour obtenir des solutions adaptées à votre situation financière compliquée. (Passage 2)
  7. La Caisse d'Epargne Rhône Alpes considère que c’est l’une de ses responsabilités sociétales d’être une banque inclusive et engagée pour être utile à nos clients, en proposant un dispositif d’écoute et d’accueil des clients en situation de fragilité, du fait d’un handicap ou de difficultés financières, permettant d’adapter ses services à leurs besoins spécifiques et de maintenir en toute situation une écoute attentive et des solutions personnalisées. (Passage 2)















































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































































In [221]:
# len(llm.tokenize(format_rag_prompt_init(query, query_results).encode(encoding='utf-8')))

1889

In [422]:
# reformulate query

query_reformulate_system_prompt = """\
Vous êtes un interprète conversationnel pour une conversation entre un utilisateur et \
un assistant IA spécialiste des produits et services de la Caisse d'Epargne Rhône-Alpes, \
une banque régionale française. \n \
L'utilisateur vous posera une question sans contexte. \
Vous devez reformuler la question pour prendre en compte le contexte de la conversation. \n \
Vous devez supposer que la question est liée aux produits et services de la Caisse d'Epargne Rhône-Alpes. \n \
Vous devez également consulter l'historique de la conversation ci-dessous lorsque vous reformulez la question. \
Par exemple, vous remplacerez les pronoms par les noms les plus probables dans l'historique de la conversation. \n \
Lorsque vous reformulez la question, accordez plus d'importance à la dernière question et \
à la dernière réponse dans l'historique des conversations. \n \
L'historique des conversations est présenté dans l'ordre chronologique inverse, \
de sorte que l'échange le plus récent se trouve en haut de la page. \n \
Répondez en seulement une phrase avec la question reformulée. \n\n \
\
Historique de la conversation : \n\n \
"""

def format_prompt_reformulate_query(query):

    system_prompt = query_reformulate_system_prompt

    for i in reversed(range(len(chat_history))):
        system_prompt += chat_history[i]["user"]
        system_prompt += chat_history[i]["assistant"]
    
    prompt = ""
    prompt = f"<|system|>\n{system_prompt.strip()} \n</s>\n"
    prompt += f"<|user|>\nPeux-tu reformuler la question suivante : \n \"{query}\" \n</s>\n"
    prompt += f"<|assistant|> Question reformulée : \n\""
    
    return prompt

In [423]:
query2 = "Peux-tu m'en dire plus au sujet de l'affacturage ?"
# print(format_prompt_reformulate_query(query2))

In [424]:
def answer_reformulate_query(query):
    
    prompt = format_prompt_reformulate_query(query)
    
    ans = answer(prompt)

    if ans.endswith('"'):
        ans = ans[:-1]
    
    return ans

In [425]:
query2_reformulated = answer_reformulate_query(query2)

Llama.generate: prefix-match hit

llama_print_timings:        load time =     575.42 ms
llama_print_timings:      sample time =     194.11 ms /    57 runs   (    3.41 ms per token,   293.65 tokens per second)
llama_print_timings: prompt eval time =    2261.49 ms /   923 tokens (    2.45 ms per token,   408.14 tokens per second)
llama_print_timings:        eval time =    1376.69 ms /    56 runs   (   24.58 ms per token,    40.68 tokens per second)
llama_print_timings:       total time =    3800.97 ms


In [426]:
query2_results = query_collection(query2_reformulated)

In [413]:
# TEST

query2_context = format_passages(query2_results)

history = ""
for i in reversed(range(len(chat_history))):
    history += chat_history[i]["user"]
    history += chat_history[i]["assistant"]
    history += "\n-----\n"

prompt = format_rag_prompt(query2_reformulated, query2_context, history)

In [414]:
print(prompt)

<|system|>
Vous êtes un assistant IA qui répond à la question posée par l'utilisateur en utilisant un contexte répertorié ci-dessous dans la rubrique Contexte.
Le contexte est formé de passages exraits du site web commercial de la Caisse d'Epargne Rhône-Alpes, une banque française régionale.
Pour répondre, tenez également compte de l'historique de la conversation qui est répertorié ci-dessous dans la rubrique Historique.
Votre réponse ne doit pas introduire des informations déjà présentes dans l'historique.
Vous recevez une pénalité de $100 à chaque fois que votre réponse répète une information déjà présente dans l'historique.
Vous fournissez avec soin des réponses précises, factuelles, réfléchies et nuancées, et vous êtes doué pour le raisonnement.
Toutes les informations factuelles que vous utilisez pour répondre proviennent exclusivement du contexte.
Si vous ne pouvez pas répondre à la question sur la base des éléments du contexte, dites simplement que vous ne savez pas, n'essayez p

In [427]:
ans = answer_rag_prompt(query2_reformulated, query2_results)

Llama.generate: prefix-match hit

llama_print_timings:        load time =     575.42 ms
llama_print_timings:      sample time =    1201.36 ms /   353 runs   (    3.40 ms per token,   293.83 tokens per second)
llama_print_timings: prompt eval time =   13189.84 ms /  3730 tokens (    3.54 ms per token,   282.79 tokens per second)
llama_print_timings:        eval time =   13559.00 ms /   352 runs   (   38.52 ms per token,    25.96 tokens per second)
llama_print_timings:       total time =   27777.04 ms


In [428]:
display(Markdown(ans))

1.  La Caisse d'Epargne Rhône Alpes propose l'affacturage, une solution pour optimiser votre trésorerie sans attendre le règlement de vos factures clients. (Passage 1)
  2. Avec l'affacturage, vous pouvez obtenir un financement adapté à votre situation financière compliquée et éviter les problèmes de trésorerie liés au délai d'attente des paiements de vos clients. (Passage 1)
  3. Cette solution permet également de préserver votre image auprès de vos fournisseurs en vous donnant la possibilité de régler leurs factures à l'horaire convenu, même si les paiements de vos clients sont retardés. (Passage 1)
  4. L'affacturage est une solution courante utilisée par de nombreuses entreprises pour optimiser leur trésorerie et gérer efficacement leurs flux de trésorerie. (Passage 1)
  5. La Caisse d'Epargne Rhône Alpes vous propose également un simulateur pour obtenir une préconisation sur le mode de financement le plus adapté à votre usage ainsi que de nombreuses informations sur la fiscalité automobile. (Passage 1)
  6. N'hésitez pas à contacter votre conseiller en ligne, à l'agence ou par téléphone pour obtenir des solutions adaptées à votre situation financière

# Generate a HTML representation of the tree structure of the webages by categories

## Create the tree structure of the tags (i.e., subparts of the URLs)

In [ ]:
tags = {}

txt_folder = 'docs/cera2'

for filename in os.listdir(txt_folder):
    if filename.endswith('.txt'):
        file_path = os.path.join(txt_folder, filename)
        with open(file_path, 'r') as file:
            file_contents = file.read()
            contents_lst = [str.replace('\n',' ').replace('\xa0', ' ') for str in file_contents.split('\n\n')]
            url = contents_lst[0]
            if '?' in url: # URLs with a '?' corresponds to call to services and have no useful content
                continue
            title = contents_lst[1]
            if not title: # when the title is absent (or empty), the page has no interest
                continue
            prefix = 'https://www.caisse-epargne.fr/'
            suffix = url.replace(prefix, '')
            parts = suffix.split('/')
            parts = [part for part in parts if part] # remove empty parts
            dic = tags
            for i, part in enumerate(parts):
                if part in dic:
                    dic[part]['nb'] = dic[part]['nb'] + 1
                else:
                    dic[part] = {'nb': 1, 'sub': {}}
                if i == len(parts)-1: # last part of an url
                    dic[part]['file'] = file_path
                
                dic = dic[part]['sub']

## Transform to HTML the tree structure of the tags

In [ ]:
def read_file_content(file_path):
    try:
        with open(file_path, 'r') as file:
            return html.escape(file.read())
    except IOError:
        return "File not found or unable to read."

def dict_to_html(d):
    html = '<ul>'
    for key, value in d.items():
        file_path = value.get('file', '')
        if 'sub' in value and value['sub']:
            html += f'<li>{key} (nb: {value["nb"]})</li>'
            html += dict_to_html(value['sub'])
        else:
            content = read_file_content(file_path) if file_path else ''
            html += f'<li data-file="{file_path}">{key} (nb: {value["nb"]})</li>'
            html += f'<pre class="file-content" style="display: none;">{content}</pre>'
    html += '</ul>'
    return html

## Add styling and javascript navigation to the HTML tree of the tags

In [ ]:
def save_html_file(content, filename):
    html_template = f"""
    <!DOCTYPE html>
    <html lang="en">
    <head>
        <meta charset="UTF-8">
        <meta name="viewport" content="width=device-width, initial-scale=1.0">
        <title>Website Hierarchy</title>
        <style>
            ul ul {{
                display: none;
            }}
            li {{
                cursor: pointer;
            }}
            .file-content {{
                display: none;
                margin-left: 20px;
                white-space: pre-wrap; /* Ensures formatting of text files is preserved */
            }}
        </style>
    </head>
    <body>
        {content}
        <script>
            document.addEventListener('DOMContentLoaded', (event) => {{
                document.querySelectorAll('li').forEach(item => {{
                    item.addEventListener('click', (e) => {{
                        e.stopPropagation();
                        let nextElement = item.nextElementSibling;
                        if (nextElement && nextElement.tagName === 'UL') {{
                            nextElement.style.display = nextElement.style.display === 'none' ? 'block' : 'none';
                        }}
                    }});
                }});
                document.querySelectorAll('li[data-file]').forEach(item => {{
                    item.addEventListener('click', (e) => {{
                        e.stopPropagation();
                        let nextElement = item.nextElementSibling;
                        if (nextElement && nextElement.tagName === 'PRE') {{
                            nextElement.style.display = nextElement.style.display === 'none' ? 'block' : 'none';
                        }}
                    }});
                }});
            }});
        </script>
    </body>
    </html>
    """
    with open(filename, 'w') as file:
        file.write(html_template)

## Generate the HTML representation of the tree of tags

In [ ]:
html_content = dict_to_html(tags)
save_html_file(html_content, 'cera_hierarchy.html')

In [ ]:
query = "query: En tant que professionnel, comment mieux gérer sa trésorerie ?"
query_embedding = embed_model.encode(query, normalize_embeddings=True)
query_embedding = query_embedding.tolist()
collection.query(
    query_embeddings=query_embedding,
    n_results=10,
    where={"category": "professionnels"},
)

# Chat interface

## Generate an answer taking into account the history of interactions

In [ ]:
history_trace = []

In [ ]:
def generate_text(message, history):
    history_trace = history
    temp = ""
    prompt = f"<|system|>\n{system_prompt}</s>\n"
    for interaction in history:
        prompt += "<|user|>\n"      + str(interaction[0]) + " </s>\n "
        prompt += "<|assistant|>\n" + str(interaction[1]) + " </s>\n"

    prompt += "<|user|>\n" + str(message) + " </s>\n <|assistant|>\n "

    output = llm(
        prompt = prompt,
        temperature=0.1,
        mirostat_mode = 2,
        max_tokens=-1,
        stop=['</s>'],
        stream=True,
    )
    for out in output:
        stream = copy.deepcopy(out)
        temp += stream["choices"][0]["text"]
        yield temp

In [ ]:
prompt = "Connais-tu des répliques dites par Charlie Munger lors des rencontres annuels organisées par Berkshire Hathaway ?"
prompt_encoded = prompt.encode(encoding='utf-8')
len(llm.tokenize(prompt_encoded))

## Gradio interface

In [ ]:
demo = gr.ChatInterface(
    generate_text,
    title="CERA",
    description="CERA RAG",
    examples=["Qui sont les philosophes les plus influencés par Hegel ?"],
    cache_examples=False,
    retry_btn=None,
    undo_btn="Delete Previous",
    clear_btn="Clear",
)
demo.queue()
demo.launch()